## Model Evaluation - Random Forest Models on Diff Data
USA World Series Results,

Run on Contestable Kickoff "bins" only

In [4]:
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
import seaborn as sns
%matplotlib inline

In [5]:
#Import Data - USA's differential data
df = pd.read_csv('../data/output/binned_KOs_diffdata.csv')
df.head()

#Import validation data
#valdf = pd.read_csv('../data/output/new_features_diffdata_validate.csv')
#valdf.head()

Opp      Tournament  Poss_Time_Diff  Score_Diff  Conv_Diff  \
0    AUSTRALIA  2015_Cape_Town       13.966480  -10.638298 -14.285714   
1        WALES  2015_Cape_Town        7.471264   15.555556  14.285714   
2        KENYA  2015_Cape_Town      -33.136095  -44.444444 -33.333333   
3  NEW ZEALAND  2015_Cape_Town       51.758794   33.333333  33.333333   
4         FIJI  2015_Cape_Town       12.880562  -20.833333 -25.000000   

   Tries_Diff  Passes_Diff  Contestable_KO_Win_pct_Diff  PenFK_Against_Diff  \
0    0.250000    25.925926                   -50.000000            0.000000   
1    0.083333    27.868852                    25.000000          -20.000000   
2   -0.750000   -10.638298                   -16.666667           66.666667   
3    0.000000    76.119403                   -75.000000          -50.000000   
4    0.266667    38.461538                   -66.666667          -33.333333   

   RuckMaul_Diff   ...    Lineout_Win_Pct_Diff  Scrum_Win_Pct_Diff  \
0       0.000000   ...                0.333333                 1.0   
1    -100.000000   ...               -1.000000                 0.0   
2      60.000000   ...               -1.000000                 0.0   
3    -100.000000   ...                0.000000                -1.0   
4     -33.333333   ...               -1.000000                 0.0   

   Less than -75  -50 : -75  -25 : -49  24 : -24  25 : 49  50 : 75  \
0            0.0      100.0        0.0       0.0      0.0      0.0   
1            0.0        0.0        0.0       0.0    100.0      0.0   
2            0.0        0.0        0.0     100.0      0.0      0.0   
3            0.0      100.0        0.0       0.0      0.0      0.0   
4            0.0      100.0        0.0       0.0      0.0      0.0   

   More than 75  Result  
0           0.0       0  
1           0.0       1  
2           0.0       0  
3           0.0       1  
4           0.0       0  

[5 rows x 22 columns]

## Randomize Data

In [6]:
#Shuffle dataframes before running model to prevent overfitting
from sklearn.utils import shuffle
df = shuffle(df)
#valdf = shuffle(valdf)

In [7]:
#Diagnostic
#df.info()
list(df.columns)
#df.head()

['Opp',
 'Tournament',
 'Poss_Time_Diff',
 'Score_Diff',
 'Conv_Diff',
 'Tries_Diff',
 'Passes_Diff',
 'Contestable_KO_Win_pct_Diff',
 'PenFK_Against_Diff',
 'RuckMaul_Diff',
 'Ruck_Win_pct_Diff',
 'Cards_diff',
 'Lineout_Win_Pct_Diff',
 'Scrum_Win_Pct_Diff',
 'Less than -75',
 '-50 : -75',
 '-25 : -49',
 '24 : -24',
 '25 : 49',
 '50 : 75',
 'More than 75',
 'Result']

In [8]:
from sklearn.model_selection import train_test_split

In [9]:
#Create a list of features to drop that are unneccessary or will bias the prediction
droplist = ['Opp','Tournament','Poss_Time_Diff','Score_Diff','Conv_Diff','Tries_Diff','Passes_Diff','Contestable_KO_Win_pct_Diff','PenFK_Against_Diff','RuckMaul_Diff','Ruck_Win_pct_Diff','Cards_diff','Lineout_Win_Pct_Diff','Scrum_Win_Pct_Diff']

rf_data = df.drop((droplist), axis=1)

#Drop rows with Result == "T" (Ties). This label messes up classification models
rf_data.drop(rf_data[rf_data.Result == 2].index, inplace=True)

#Pull out the variable we're trying to predict: 'Result'
X = rf_data.drop('Result',axis=1)
y = rf_data['Result']

In [10]:
rf_data.head()
#Check to ensure 'Result' only contains 2 values (W, L)
#rf_data['Result'].describe()
#rf_data.describe()

Less than -75  -50 : -75  -25 : -49  24 : -24  25 : 49  50 : 75  \
52             0.0        0.0        0.0       0.0    100.0      0.0   
8              0.0        0.0      100.0       0.0      0.0      0.0   
165            0.0      100.0        0.0       0.0      0.0      0.0   
127            0.0        0.0        0.0     100.0      0.0      0.0   
164            0.0        0.0      100.0       0.0      0.0      0.0   

     More than 75  Result  
52            0.0       1  
8             0.0       1  
165           0.0       1  
127           0.0       0  
164           0.0       1

In [11]:
#Pull out the variable we're trying to predict: 'Result'
X = rf_data.drop('Result',axis=1)
y = rf_data['Result']
#X_train, X_test, y_train, y_test = train_test_split( X, y, test_size=0.30)

In [12]:
#Split into train/test/validate sets
#OR, keep as is and use new data for validate
#156 rows in original dataframe
X_train, X_test, y_train, y_test = train_test_split(X, y, test_size=0.3, random_state=101)

### Validation set
Imported last two series stops (London & Paris, 2018 - 12 matches total) to use as a validation set.

Need to also incorporate into larger data set later.

#Drop features that are unneccessary/str or will bias the prediction
val_data = valdf.drop((droplist), axis=1)

#Drop rows with Result == "T" (Ties). This label messes up classification models
val_data.drop(val_data[val_data.Result == 2].index, inplace=True)

#Pull out the variable we're trying to predict: 'Result'
val_X = val_data.drop('Result',axis=1)
val_y = val_data['Result']

## Random Forest

In [13]:
from sklearn.ensemble import RandomForestClassifier

#Fit RF Classifier model
rf = RandomForestClassifier(random_state=101)

from pprint import pprint
# Look at parameters used by our current forest
print('Default Parameters currently in use:\n')
pprint(rf.get_params())

Default Parameters currently in use:

{'bootstrap': True,
 'class_weight': None,
 'criterion': 'gini',
 'max_depth': None,
 'max_features': 'auto',
 'max_leaf_nodes': None,
 'min_impurity_decrease': 0.0,
 'min_impurity_split': None,
 'min_samples_leaf': 1,
 'min_samples_split': 2,
 'min_weight_fraction_leaf': 0.0,
 'n_estimators': 10,
 'n_jobs': 1,
 'oob_score': False,
 'random_state': 101,
 'verbose': 0,
 'warm_start': False}


## Evaluate Base Model

In [14]:
from sklearn.metrics import accuracy_score

In [15]:
base_model = RandomForestClassifier(n_estimators = 10, random_state = 101)
base_model.fit(X_train, y_train)
predictions = base_model.predict(X_test)
#base_accuracy = evaluate(base_model, y_train, y_test)

#Use sklearn.metrics 'accuracy_score' to determine accuracy of trained and test model
base_train_acc = accuracy_score(y_train, base_model.predict(X_train))
base_test_acc = accuracy_score(y_test, predictions)
print("Base Model")
print('Train:')
print(base_train_acc)
print('Test:')
print(base_test_acc)

Base Model
Train:
0.5625
Test:
0.551020408163


### Hyperparameters
* n_estimators = number of trees in the foreset
* max_features = max number of features considered for splitting a node
* max_depth = max number of levels in each decision tree
* min_samples_split = min number of data points placed in a node before the node is split
* min_samples_leaf = min number of data points allowed in a leaf node
* bootstrap = method for sampling data points (with or without replacement)

### Grid Search with Cross Validation
Random search allowed us to narrow down the range for each hyperparameter. Now that we know where to concentrate our search, we can explicitly specify every combination of settings to try. We do this with GridSearchCV, a method that, instead of sampling randomly from a distribution, evaluates all combinations we define.

In [16]:
from sklearn.model_selection import GridSearchCV
# Create the parameter grid based on the results of random search 
param_grid = {
    'bootstrap': [True, False],
    'max_depth': [60, 70, 80, 90, 100, 110],
    'max_features': [4, 5, 6],
    'min_samples_leaf': [1, 2, 3, 4, 5],
    'min_samples_split': [2, 5, 8, 10, 12],
    'n_estimators': [100, 200, 300, 400, 600]
}

# Create a base model
#rf = RandomForestClassifier(random_state = 101)
# Instantiate the grid search model
grid_search = GridSearchCV(estimator = rf, param_grid = param_grid, 
                          cv = 5, scoring = 'accuracy', n_jobs = -1, verbose = 2)

In [17]:
# Fit the grid search to the data
grid_search.fit(X_train, y_train)
grid_search.best_params_

best_grid = grid_search.best_estimator_
#grid_accuracy = evaluate(best_grid, X_test, y_test)

#get predictions with best parameters
grid_predict = best_grid.predict(X_test)

grid_train_acc = accuracy_score(y_train, best_grid.predict(X_train))
grid_test_acc = accuracy_score(y_test, grid_predict)

#print('Improvement of {:0.2f}%.'.format( 100 * (grid_test_acc - base_test_acc) / base_test_acc))

Fitting 5 folds for each of 4500 candidates, totalling 22500 fits
[CV] bootstrap=True, max_depth=60, max_features=4, min_samples_leaf=1, min_samples_split=2, n_estimators=100 
[CV] bootstrap=True, max_depth=60, max_features=4, min_samples_leaf=1, min_samples_split=2, n_estimators=100 
[CV] bootstrap=True, max_depth=60, max_features=4, min_samples_leaf=1, min_samples_split=2, n_estimators=100 
[CV] bootstrap=True, max_depth=60, max_features=4, min_samples_leaf=1, min_samples_split=2, n_estimators=100 
[CV]  bootstrap=True, max_depth=60, max_features=4, min_samples_leaf=1, min_samples_split=2, n_estimators=100, total=   0.3s
[CV]  bootstrap=True, max_depth=60, max_features=4, min_samples_leaf=1, min_samples_split=2, n_estimators=100, total=   0.3s
[CV] bootstrap=True, max_depth=60, max_features=4, min_samples_leaf=1, min_samples_split=2, n_estimators=100 
[CV]  bootstrap=True, max_depth=60, max_features=4, min_samples_leaf=1, min_samples_split=2, n_estimators=100, total=   0.3s
[CV] boot

[Parallel(n_jobs=-1)]: Done  33 tasks      | elapsed:    7.4s


[CV]  bootstrap=True, max_depth=60, max_features=4, min_samples_leaf=1, min_samples_split=5, n_estimators=200, total=   0.6s
[CV] bootstrap=True, max_depth=60, max_features=4, min_samples_leaf=1, min_samples_split=5, n_estimators=300 
[CV]  bootstrap=True, max_depth=60, max_features=4, min_samples_leaf=1, min_samples_split=5, n_estimators=200, total=   0.6s
[CV] bootstrap=True, max_depth=60, max_features=4, min_samples_leaf=1, min_samples_split=5, n_estimators=300 
[CV]  bootstrap=True, max_depth=60, max_features=4, min_samples_leaf=1, min_samples_split=5, n_estimators=300, total=   0.8s
[CV] bootstrap=True, max_depth=60, max_features=4, min_samples_leaf=1, min_samples_split=5, n_estimators=300 
[CV]  bootstrap=True, max_depth=60, max_features=4, min_samples_leaf=1, min_samples_split=5, n_estimators=300, total=   0.8s
[CV] bootstrap=True, max_depth=60, max_features=4, min_samples_leaf=1, min_samples_split=5, n_estimators=400 
[CV]  bootstrap=True, max_depth=60, max_features=4, min_samp

[CV]  bootstrap=True, max_depth=60, max_features=4, min_samples_leaf=1, min_samples_split=8, n_estimators=400, total=   1.5s
[CV] bootstrap=True, max_depth=60, max_features=4, min_samples_leaf=1, min_samples_split=8, n_estimators=600 
[CV]  bootstrap=True, max_depth=60, max_features=4, min_samples_leaf=1, min_samples_split=8, n_estimators=400, total=   1.5s
[CV] bootstrap=True, max_depth=60, max_features=4, min_samples_leaf=1, min_samples_split=8, n_estimators=600 
[CV]  bootstrap=True, max_depth=60, max_features=4, min_samples_leaf=1, min_samples_split=8, n_estimators=600, total=   2.1s
[CV] bootstrap=True, max_depth=60, max_features=4, min_samples_leaf=1, min_samples_split=8, n_estimators=600 
[CV]  bootstrap=True, max_depth=60, max_features=4, min_samples_leaf=1, min_samples_split=8, n_estimators=600, total=   2.0s
[CV] bootstrap=True, max_depth=60, max_features=4, min_samples_leaf=1, min_samples_split=10, n_estimators=100 
[CV]  bootstrap=True, max_depth=60, max_features=4, min_sam

[CV]  bootstrap=True, max_depth=60, max_features=4, min_samples_leaf=1, min_samples_split=12, n_estimators=100, total=   0.4s
[CV] bootstrap=True, max_depth=60, max_features=4, min_samples_leaf=1, min_samples_split=12, n_estimators=200 
[CV]  bootstrap=True, max_depth=60, max_features=4, min_samples_leaf=1, min_samples_split=12, n_estimators=200, total=   0.7s
[CV] bootstrap=True, max_depth=60, max_features=4, min_samples_leaf=1, min_samples_split=12, n_estimators=200 
[CV]  bootstrap=True, max_depth=60, max_features=4, min_samples_leaf=1, min_samples_split=12, n_estimators=200, total=   0.7s
[CV] bootstrap=True, max_depth=60, max_features=4, min_samples_leaf=1, min_samples_split=12, n_estimators=200 
[CV]  bootstrap=True, max_depth=60, max_features=4, min_samples_leaf=1, min_samples_split=12, n_estimators=200, total=   0.7s
[CV] bootstrap=True, max_depth=60, max_features=4, min_samples_leaf=1, min_samples_split=12, n_estimators=300 
[CV]  bootstrap=True, max_depth=60, max_features=4, 

...

[CV] bootstrap=False, max_depth=110, max_features=6, min_samples_leaf=5, min_samples_split=2, n_estimators=300 
[CV]  bootstrap=False, max_depth=110, max_features=6, min_samples_leaf=4, min_samples_split=12, n_estimators=600, total=   2.6s
[CV] bootstrap=False, max_depth=110, max_features=6, min_samples_leaf=5, min_samples_split=2, n_estimators=300 
[CV]  bootstrap=False, max_depth=110, max_features=6, min_samples_leaf=5, min_samples_split=2, n_estimators=200, total=   0.9s
[CV] bootstrap=False, max_depth=110, max_features=6, min_samples_leaf=5, min_samples_split=2, n_estimators=300 
[CV]  bootstrap=False, max_depth=110, max_features=6, min_samples_leaf=5, min_samples_split=2, n_estimators=200, total=   0.8s
[CV] bootstrap=False, max_depth=110, max_features=6, min_samples_leaf=5, min_samples_split=2, n_estimators=300 
[CV]  bootstrap=False, max_depth=110, max_features=6, min_samples_leaf=5, min_samples_split=2, n_estimators=300, total=   1.2s
[CV] bootstrap=False, max_depth=110, max_fe

[CV]  bootstrap=False, max_depth=110, max_features=6, min_samples_leaf=5, min_samples_split=5, n_estimators=400, total=   2.3s
[CV] bootstrap=False, max_depth=110, max_features=6, min_samples_leaf=5, min_samples_split=5, n_estimators=600 
[CV]  bootstrap=False, max_depth=110, max_features=6, min_samples_leaf=5, min_samples_split=5, n_estimators=400, total=   2.3s
[CV] bootstrap=False, max_depth=110, max_features=6, min_samples_leaf=5, min_samples_split=5, n_estimators=600 
[CV]  bootstrap=False, max_depth=110, max_features=6, min_samples_leaf=5, min_samples_split=5, n_estimators=400, total=   2.5s
[CV] bootstrap=False, max_depth=110, max_features=6, min_samples_leaf=5, min_samples_split=5, n_estimators=600 
[CV]  bootstrap=False, max_depth=110, max_features=6, min_samples_leaf=5, min_samples_split=5, n_estimators=400, total=   2.5s
[CV] bootstrap=False, max_depth=110, max_features=6, min_samples_leaf=5, min_samples_split=5, n_estimators=600 
[CV]  bootstrap=False, max_depth=110, max_fe

[CV] bootstrap=False, max_depth=110, max_features=6, min_samples_leaf=5, min_samples_split=10, n_estimators=100 
[CV]  bootstrap=False, max_depth=110, max_features=6, min_samples_leaf=5, min_samples_split=8, n_estimators=600, total=   2.5s
[CV] bootstrap=False, max_depth=110, max_features=6, min_samples_leaf=5, min_samples_split=10, n_estimators=200 
[CV]  bootstrap=False, max_depth=110, max_features=6, min_samples_leaf=5, min_samples_split=10, n_estimators=100, total=   0.5s
[CV] bootstrap=False, max_depth=110, max_features=6, min_samples_leaf=5, min_samples_split=10, n_estimators=200 
[CV]  bootstrap=False, max_depth=110, max_features=6, min_samples_leaf=5, min_samples_split=10, n_estimators=100, total=   0.5s
[CV] bootstrap=False, max_depth=110, max_features=6, min_samples_leaf=5, min_samples_split=10, n_estimators=200 
[CV]  bootstrap=False, max_depth=110, max_features=6, min_samples_leaf=5, min_samples_split=10, n_estimators=200, total=   0.8s
[CV] bootstrap=False, max_depth=110, 

[CV]  bootstrap=False, max_depth=110, max_features=6, min_samples_leaf=5, min_samples_split=12, n_estimators=300, total=   1.2s
[CV] bootstrap=False, max_depth=110, max_features=6, min_samples_leaf=5, min_samples_split=12, n_estimators=300 
[CV]  bootstrap=False, max_depth=110, max_features=6, min_samples_leaf=5, min_samples_split=12, n_estimators=300, total=   1.2s
[CV] bootstrap=False, max_depth=110, max_features=6, min_samples_leaf=5, min_samples_split=12, n_estimators=400 
[CV]  bootstrap=False, max_depth=110, max_features=6, min_samples_leaf=5, min_samples_split=12, n_estimators=300, total=   1.2s
[CV] bootstrap=False, max_depth=110, max_features=6, min_samples_leaf=5, min_samples_split=12, n_estimators=400 
[CV]  bootstrap=False, max_depth=110, max_features=6, min_samples_leaf=5, min_samples_split=12, n_estimators=300, total=   1.2s
[CV] bootstrap=False, max_depth=110, max_features=6, min_samples_leaf=5, min_samples_split=12, n_estimators=400 
[CV]  bootstrap=False, max_depth=110

[Parallel(n_jobs=-1)]: Done 22500 out of 22500 | elapsed: 127.4min finished


In [18]:
print("Base Model")
print(base_train_acc)
print(base_test_acc)

print("\n")
print("Grid Search Model")
print(grid_train_acc)
print(grid_test_acc)

Base Model
0.5625
0.551020408163


Grid Search Model
0.571428571429
0.551020408163


In [20]:
print('Improvement of {:0.2f}%.'.format( 100 * (grid_test_acc - base_test_acc) / base_test_acc))

Improvement of 0.00%.


### Grid Search Accuracy Results
**Base Model**
```
0.5625
0.551020408163
```
**Grid Search Model**
```
0.571428571429
0.551020408163
```

***Improvement of 0% on test data***

In [21]:
grid_search.best_params_

{'bootstrap': True,
 'max_depth': 60,
 'max_features': 4,
 'min_samples_leaf': 3,
 'min_samples_split': 2,
 'n_estimators': 200}

In [22]:
# examine the best model#
print('Best Estimator:')
print(grid_search.best_estimator_)
print()
print('Best Score:')
print(grid_search.best_score_)
print()
print('Best Parameters:')
print(grid_search.best_params_)

Best Estimator:
RandomForestClassifier(bootstrap=True, class_weight=None, criterion='gini',
            max_depth=60, max_features=4, max_leaf_nodes=None,
            min_impurity_decrease=0.0, min_impurity_split=None,
            min_samples_leaf=3, min_samples_split=2,
            min_weight_fraction_leaf=0.0, n_estimators=200, n_jobs=1,
            oob_score=False, random_state=101, verbose=0, warm_start=False)

Best Score:
0.473214285714

Best Parameters:
{'bootstrap': True, 'max_depth': 60, 'max_features': 4, 'min_samples_leaf': 3, 'min_samples_split': 2, 'n_estimators': 200}


**Best Estimator**
```
RandomForestClassifier(bootstrap=True, class_weight=None, criterion='gini',
            max_depth=60, max_features=4, max_leaf_nodes=None,
            min_impurity_decrease=0.0, min_impurity_split=None,
            min_samples_leaf=3, min_samples_split=2,
            min_weight_fraction_leaf=0.0, n_estimators=200, n_jobs=1,
            oob_score=False, random_state=101, verbose=0, warm_start=False)
```

**Best Score**
```
0.473214285714
```
**Best Parameters**
```
{'bootstrap': True, 'max_depth': 60, 'max_features': 4, 'min_samples_leaf': 3, 'min_samples_split': 2, 'n_estimators': 200}
```

### Use new parameters from gridsearch to create and fit model

In [23]:
#Fit classifier with new model parameters from gridsearch
rfc = RandomForestClassifier(bootstrap=True, class_weight=None, criterion='gini',
            max_depth=60, max_features=4, max_leaf_nodes=None,
            min_impurity_decrease=0.0, min_impurity_split=None,
            min_samples_leaf=3, min_samples_split=2,
            min_weight_fraction_leaf=0.0, n_estimators=200, n_jobs=1,
            oob_score=False, random_state=101, verbose=0, warm_start=False)

#Fit model
rfc.fit(X_train, y_train)

#Predict Classifier
rfc_pred = rfc.predict(X_test)

## Random Forest Model Eval

In [24]:
#Accuracy
rfc_acc = accuracy_score(y_test, rfc_pred)
print(rfc_acc)

0.551020408163


In [25]:
#Find Feature Importances
feature_importances = pd.DataFrame(rfc.feature_importances_,
                                   index = X_train.columns,
                                    columns=['importance']).sort_values('importance', ascending=False)

print("Feature Importance")
print(feature_importances)

Feature Importance
               importance
50 : 75          0.460128
24 : -24         0.165265
-25 : -49        0.121669
-50 : -75        0.120798
25 : 49          0.119974
More than 75     0.012166
Less than -75    0.000000


In [26]:
from sklearn.metrics import classification_report,confusion_matrix,accuracy_score

#Output confusion matrix
print("Confusion Matrix")
print(confusion_matrix(y_test,rfc_pred))

#import libraries to ignore UndefinedMetricWarning
import warnings
import sklearn.exceptions
warnings.filterwarnings("ignore", category=sklearn.exceptions.UndefinedMetricWarning)

#get the model's accuracy score
accuracy_score(y_test, rfc_pred)
print("\n")
print("Classification Report")
print(classification_report(y_test,rfc_pred))

#print accuracy score
print("\n")
print("Accuracy Score")
print(rfc.score(X_test, y_test))

Confusion Matrix
[[ 0 22]
 [ 0 27]]


Classification Report
             precision    recall  f1-score   support

          0       0.00      0.00      0.00        22
          1       0.55      1.00      0.71        27

avg / total       0.30      0.55      0.39        49



Accuracy Score
0.551020408163
